In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from pathlib import Path

try:
    from google.colab import drive

    drive.mount("/content/drive")
    workding_dir = "/content/drive/MyDrive/logical-reasoning/"
except ModuleNotFoundError:
    workding_dir = str(Path.cwd().parent)

In [3]:
import os
import sys
from pathlib import Path

os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /home/inflaton/code/projects/courses/logical-reasoning


In [4]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: /home/inflaton/code/projects/courses/logical-reasoning/.env


True

In [5]:
import os

model_name = os.getenv("MODEL_NAME")
adapter_name_or_path = os.getenv("ADAPTER_NAME_OR_PATH")
load_in_4bit = os.getenv("LOAD_IN_4BIT") == "true"
data_path = os.getenv("LOGICAL_REASONING_DATA_PATH")
results_path = os.getenv("LOGICAL_REASONING_RESULTS_PATH")
use_english_datasets = os.getenv("USE_ENGLISH_DATASETS") == "true"

print(model_name, adapter_name_or_path, load_in_4bit, data_path, results_path)

internlm/internlm2_5-7b-chat-1m llama-factory/saves/internlm2_5_7b/lora/sft_bf16_p2_full/checkpoint-88 True datasets/mgtv results/mgtv-results_internlm_best.csv


In [6]:
%%time
!python --version
!pip show flash-attn

Python 3.11.9
CPU times: user 284 ms, sys: 88 ms, total: 372 ms
Wall time: 4.21 s


In [7]:
from llm_toolkit.llm_utils import *
from llm_toolkit.logical_reasoning_utils import *

device = check_gpu()

loading /home/inflaton/code/projects/courses/logical-reasoning/llm_toolkit/logical_reasoning_utils.py
GPU is available


In [8]:
%%time

# model, tokenizer = load_model(model_name, adapter_name_or_path=adapter_name_or_path, using_llama_factory=False)
model, tokenizer = load_model(adapter_name_or_path, using_llama_factory=False)

loading model: llama-factory/saves/internlm2_5_7b/lora/sft_bf16_p2_full/checkpoint-88 with adapter: None


Loading checkpoint shards:   0%|          | 0/8 [00:00<?, ?it/s]

In [11]:
datasets = load_logical_reasoning_dataset(
    data_path,
    tokenizer=tokenizer,
    chinese_prompt=not use_english_datasets,
    using_p1=False,
)

loading train/test data files


Map:   0%|          | 0/25000 [00:00<?, ? examples/s]

Map:   0%|          | 0/3000 [00:00<?, ? examples/s]

DatasetDict({
    train: Dataset({
        features: ['text', 'label', 'answer', 'title', 'puzzle', 'truth', 'train_text', 'prompt'],
        num_rows: 25000
    })
    test: Dataset({
        features: ['text', 'label', 'answer', 'title', 'puzzle', 'truth', 'train_text', 'prompt'],
        num_rows: 3000
    })
})


In [12]:
def evaluate_model(model, tokenizer, model_name, dataset):
    print(f"Evaluating model: {model_name} on {device}")
    predictions = eval_model(model, tokenizer, dataset, device=device)

    save_results(
        model_name,
        results_path,
        dataset,
        predictions,
        debug=False,
    )

    metrics = calc_metrics(dataset["label"], predictions, debug=False)
    print(metrics)

In [13]:
%%time

evaluate_model(model, tokenizer, f"{model_name}{'_' + adapter_name_or_path if adapter_name_or_path else ''}_NV4080", datasets["test"])

Evaluating model: THUDM/glm-4-9b-chat-1m_NV4080 on cuda


  0%|          | 1/3000 [1:24:27<4221:21:42, 5067.32s/it]

--------
step 1: 
不是
--------
step 2: 
不是
--------
step 3: 
不是
--------
step 4: 不是
--------
step 5: 不是


 13%|█▎        | 392/3000 [5:21:45<35:40:38, 49.25s/it]  


KeyboardInterrupt: 